Informatics 2 - Foundations of Data Science

# Logistic regression

David Sterratt, 2020-2024

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
from sklearn.linear_model import LogisticRegression
import matplotlib
from sklearn.neighbors import KNeighborsClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from scipy.special import expit


matplotlib.rcParams['figure.dpi'] = 200

## Logistic function

In [ ]:
x = np.arange(-10, 10, 0.1)

plt.figure(figsize=(6, 2))
plt.subplot(1, 2, 1)
plt.plot(x, expit(x), label='f(x)')
plt.legend()
# plt.annotate(, (-10, 0.8), color='blue')
plt.xlabel('x')
plt.ylabel('f(x)')
plt.tight_layout()
plt.savefig('logistic.pdf')
plt.savefig('logistic.png')

plt.subplot(1, 2, 2)
plt.plot(x, expit(x-4), label='f(x-4)')
plt.plot(x, expit(x/2-2), label='f(x/2-2)')
plt.legend()
plt.xlabel('x')
plt.ylabel('f(x)')
plt.tight_layout()
plt.savefig('logistic.pdf')
plt.savefig('logistic.png')

## Credit Example

This is nice, but we'd need to do log transforms on the variables, apart, perhaps, from Age, which would make the explanation harder. Cleaned version of UCI credit scoring dataset: https://github.com/davidcsterratt/Credit_Shiny  https://nycdatascience.com/blog/student-works/credit-card-approval-analysis/

In [ ]:
## Loading and cleaning

credit = pd.read_csv('Credit_Approval.csv', na_values=['?'])
credit.replace('+', 1, inplace=True)
credit.replace('-', 0, inplace=True)
credit.replace('?', pd.NA, inplace=True)
credit['Gender']=credit['Gender'].replace('a', 0)
credit['Gender']=credit['Gender'].replace('b', 1)
credit['Employed']=credit['Employed'].replace('f', 0)
credit['Employed']=credit['Employed'].replace('t', 1)
credit.dropna(inplace=True)
credit.info()

In [ ]:
## Drop irrelevant (we suppose!) ZipCode
credit.drop(['ZipCode'], axis=1, inplace=True)

In [ ]:
credit.groupby('Gender').mean(numeric_only=True)

In [ ]:
plt.figure(figsize=(6,6))
# sns.set(font_scale=2)
sns.pairplot(credit.drop(['Debt', 'YearsEmployed'], axis=1), hue='Approved')
# grid_kws=dict(font_scale=10))
plt.tight_layout()
plt.savefig('credit-pairplot.png')

In [ ]:
# plt.scatter(np.log(credit['Income']+1), credit['Approved'])
# plt.xlim([0, 5000])
credit['LogIncome'] = np.log10(credit['Income'] + 1)
credit['LogCreditScore'] = np.log(credit['CreditScore'] + 1)
credit.drop(['Income', 'CreditScore'], axis=1, inplace=True)

In [ ]:
sns.pairplot(credit.drop(['Debt', 'YearsEmployed'], axis=1), hue='Approved')
plt.savefig('credit-pairplot.png')

In [ ]:
credit.drop(['Debt', 'YearsEmployed'], axis=1).corr()

In [ ]:
# sns.set(font_scale=1)

credit_sorted = credit.sort_values('Age')
plt.figure(figsize=(3, 1.5))
sns.scatterplot(x='Age', y='Approved', data=credit_sorted.sample(50, random_state=1))
plt.tight_layout()
plt.savefig('credit-age.pdf')
plt.savefig('credit-age.png')

In [ ]:
X = credit_sorted[['Age']].to_numpy(copy=True) 
y = credit_sorted['Approved'].to_numpy()
clf = LogisticRegression(random_state=0).fit(X, y)
beta0 = clf.intercept_
beta1 = clf.coef_[0][0]
plt.figure(figsize=(3, 2))

sns.scatterplot(x='Age', y='Approved', data=credit_sorted.sample(50, random_state=1))
plt.plot(X, clf.predict_proba(X)[:,1])
plt.annotate('$\\hat\\beta_0=%2.3f$'%(beta0), (20, 0.8))
plt.annotate('$\\hat\\beta_1=%2.3f$'%(beta1), (20, 0.6))

plt.tight_layout()
plt.savefig('credit-age-lr.pdf')
plt.savefig('credit-age-lr.png')

In [ ]:
# np.exp(clf.coef_)
# clf.intercept_/clf.coef_
beta0 = clf.intercept_
beta1 = clf.coef_[0][0]
print('beta_0 = %2.3f; beta_1 = %2.3f; offset = %2.3f'%(beta0, beta1, -beta0/beta1))
print('f(beta_0) = %2.3f'%(expit(beta0)))

clf.coef_

### Employment

In [ ]:
contingency_table = credit.pivot_table('Approved', 'Employed')
contingency_table['Not approved'] = 1 - contingency_table['Approved']
contingency_table['Approval odds'] = contingency_table['Approved']/contingency_table['Not approved']
contingency_table.to_latex('credit-employment-contingency.tex', float_format='%2.2f')

In [ ]:
odds_ratio = contingency_table.loc[1, 'Approval odds']/contingency_table.loc[0, 'Approval odds']
odds_ratio

In [ ]:
np.log(odds_ratio)

In [ ]:
X = credit_sorted[['Employed']].to_numpy(copy=True) 
y = credit_sorted['Approved'].to_numpy()
clf = LogisticRegression(random_state=0).fit(X, y)
sns.relplot(x='Employed', y='Approved', data=credit_sorted.sample(50, random_state=1))
plt.plot(X, clf.predict_proba(X)[:,1])

## Both age and Employed

In [ ]:
X = credit_sorted[['Age', 'Employed']].to_numpy(copy=True) 
y = credit_sorted['Approved'].to_numpy()
logr = LogisticRegression(random_state=0).fit(X, y)
np.exp(logr.coef_)[0]
logr.coef_

In [ ]:
beta = np.array([logr.intercept_[0], logr.coef_[0][0], logr.coef_[0][1]])
beta

In [ ]:
credit_age_employment = pd.DataFrame({'Variable': ['Intercept', 'Age', 'Employed'],
                                      'Coefficient': beta,
                                     'Odds or OR': np.exp(beta)})
credit_age_employment.index=['$\\hat\\beta_0$', '$\\hat\\beta_1$', '$\\hat\\beta_2$']
# credit_age_employment.to_latex('credit-employment-age-coeffs.tex', float_format='%2.3f')
credit_age_employment

## Age and LogIncome

In [ ]:
X = credit_sorted[['Age', 'LogIncome']].to_numpy(copy=True) 
y = credit_sorted['Approved'].to_numpy()
logr = LogisticRegression(random_state=0).fit(X, y)
np.exp(logr.coef_)[0]
logr.coef_
logr.score(X, y)

In [ ]:
sns.scatterplot(x='Age', y='LogIncome', hue='Approved', data=credit_sorted)
x1 = np.arange(10, 90, 10)
beta0 = logr.intercept_
beta1 = logr.coef_[0][0]
beta2 = logr.coef_[0][1]
c = 0
x2 = (c - beta0-beta1*x1)/beta2
plt.plot(x1, x2, color='black')
c = np.log(3)
x2 = (c - beta0-beta1*x1)/beta2
plt.plot(x1, x2, color='gray')
c = np.log(1/3)
x2 = (c - beta0-beta1*x1)/beta2
plt.plot(x1, x2, color='gray')
plt.ylim([0, 6])
plt.xlabel('Age (years)')
plt.ylabel('Log (base 10) of Income')


plt.savefig('credit-age-logincome-decision-boundary.pdf')
plt.savefig('credit-age-logincome-decision-boundary.png')

### Scaled Logistic regression

In [ ]:
logr_scaled = Pipeline([('scaler', StandardScaler()), ('lr', LogisticRegression())])
logr_scaled.fit(X, y)
# np.exp(clf.coef_)[0]
# clf.coef_
logr_scaled.score(X, y)

### Comparison with KNN

In [ ]:
k = 15
neigh = KNeighborsClassifier(n_neighbors=k)
neigh.fit(X, y)
neigh.score(X, y)

### KNN  scaled

In [ ]:
k = 11
neigh_scaled = Pipeline([('scaler', StandardScaler()), ('knn', KNeighborsClassifier(n_neighbors=k))])
neigh_scaled.fit(X, y)
neigh_scaled.score(X, y)

In [ ]:
x_min, x_max = 10, 80
y_min, y_max =  0,  6
xx, yy = np.meshgrid(np.arange(x_min, x_max, 0.1),
                     np.arange(y_min, y_max, 0.1))

fig, ax = plt.subplots(1, 2, sharex='col', sharey='row', figsize=(6, 3))
plt.sca(ax[0])
sns.scatterplot(x='Age', y='LogIncome', hue='Approved', data=credit_sorted)

C = logr.predict(np.c_[xx.ravel(), yy.ravel()])
C = C.reshape(xx.shape)
# plt.contour(xx, yy, C, levels=[0.5])
x2 = (0 - beta0-beta1*x1)/beta2
plt.plot(x1, x2, color='black')
plt.ylim([0, 6])
plt.sca(ax[1])
sns.scatterplot(x='Age', y='LogIncome', hue='Approved', data=credit_sorted)

C = neigh_scaled.predict(np.c_[xx.ravel(), yy.ravel()])
C = C.reshape(xx.shape)
plt.contour(xx, yy, C, levels=[0.5])
plt.tight_layout()

plt.savefig('logistic-knn.png')
plt.savefig('logistic-knn.pdf')

## Boostrapping confidence intervals
We'll go back to the age and employment example.

In [ ]:
np.random.seed(0)
B = 1000
n = len(credit_sorted)

beta0star = np.zeros(B)
beta1star = np.zeros(B)
beta2star = np.zeros(B)

for i in range(B):
    credit_sample = credit_sorted.sample(n, replace=True)
    X = credit_sample[['Age', 'Employed']].to_numpy(copy=True) 
    y = credit_sample['Approved'].to_numpy()
    clf = LogisticRegression().fit(X, y)
    beta0star[i] = clf.intercept_[0]
    beta1star[i] = clf.coef_[0][0]
    beta2star[i] = clf.coef_[0][1]
  
Odds_star = pd.Series(np.exp(beta0star))
OR_age_star = pd.Series(np.exp(beta1star))
OR_employment_star = pd.Series(np.exp(beta2star))

In [ ]:
Odds_star.quantile([0.05, 0.95])

In [ ]:
OR_age_star.quantile([0.05, 0.95])

In [ ]:
OR_employment_star.quantile([0.05, 0.95])

In [ ]:
plt.figure(figsize=[6,2], dpi=200)

plt.subplot(1, 3, 1)
plt.hist(np.exp(beta0star), bins=20, density=True)
plt.xlabel('odds (Intercept)')
plt.vlines(Odds_star.quantile([0.05, 0.95]), 0, 10, color='orange')


plt.subplot(1, 3, 2)
plt.hist(np.exp(beta1star), bins=20, density=True)
plt.xlabel('OR (Year of age)')
plt.vlines(OR_age_star.quantile([0.05, 0.95]), 0, 45, color='orange')

plt.subplot(1, 3, 3)
plt.hist(np.exp(beta2star), bins=20, density=True)
plt.vlines(OR_employment_star.quantile([0.05, 0.95]), 0, 0.5, color='orange')

plt.xlabel('OR (Employment)')


plt.tight_layout()
plt.savefig('credit-employment-age-bootstrap.pdf')
plt.savefig('credit-employment-age-bootstrap.png')

## Making logistic regression transparent

In [ ]:
credit_sorted.head()

In [ ]:
X = credit_sorted[['Employed', 'Age', 'LogIncome']].to_numpy(copy=True) 
y = credit_sorted['Approved'].to_numpy()
logr = LogisticRegression(random_state=0).fit(X, y)
logr.coef_
# logr.score(X, y)

print("If you are in employment you score %2.3f, if not you score 0"%(logr.coef_[0][0]))
print("Multiply your age by %2.3f and add the result to your score"%(logr.coef_[0][1]))
print("Round your income to the nearest 1000. Multiply the number of zeros in this figure by %2.3f and add the result to your score"%(logr.coef_[0][2]))
print("If you scored more than %2.3f, your credit will be approved"%(-logr.intercept_))

-logr.intercept_


## Logistic regression on full dataset



In [ ]:
credit_full = credit.drop(['Citizen', 'DriversLicense', 'PriorDefault', 'EducationLevel', 'Ethnicity', 'BankCustomer', 'Married'], 1) 
credit_full['LogDebt'] = np.log10(credit_full['Debt'] + 1)
credit_full['LogYearsEmployed'] = np.log10(credit_full['YearsEmployed'] + 1)

credit_full.drop(['Debt'], axis=1, inplace=True)
credit_full.drop(['YearsEmployed'], axis=1, inplace=True)

sns.pairplot(credit_full, hue='Approved')


In [ ]:
X_gender = credit_full.drop(['Approved'], axis=1).to_numpy(copy=True) 
y = credit['Approved'].to_numpy()

logr_gender = LogisticRegression(random_state=0).fit(X_gender, y)

coeffs_gender = pd.Series({'Intercept': logr_gender.intercept_})
coeffs_gender = coeffs_gender.append(pd.Series(logr_gender.coef_[0], index=credit_full.columns.drop('Approved')))

logr_gender.score(X_gender, y)

In [ ]:
coeffs_gender

In [ ]:
X_nogender = credit_full.drop(['Approved', 'Gender'], axis=1).to_numpy(copy=True) 
y = credit['Approved'].to_numpy()

logr_nogender = LogisticRegression(random_state=0).fit(X_nogender, y)

coeffs_nogender = pd.Series({'Intercept': logr_nogender.intercept_})
coeffs_nogender = coeffs_nogender.append(pd.Series(logr_nogender.coef_[0], index=credit_full.columns.drop(['Approved', 'Gender'])))

logr_nogender.score(X_nogender, y)

In [ ]:
coeffs_nogender

In [ ]:
personA = pd.Series({'Gender': 1,
                     'Age': 30,
                     'Employed': 1,
                     'LogIncome': 3.1,
                     'LogCreditScore': 0,
                     'LogDebt': 0, 
                     'LogYearsEmployed': np.log10(5)})

personB = personA.copy()
personB['Gender'] = 0

np.sum(personA * coeffs_nogender.drop('Intercept')) + coeffs_nogender['Intercept']
np.sum(personB * coeffs_nogender.drop('Intercept')) + coeffs_nogender['Intercept']

In [ ]:
print(np.sum(personA * coeffs_gender.drop('Intercept')) + coeffs_nogender['Intercept'])
print(np.sum(personB * coeffs_gender.drop('Intercept')) + coeffs_nogender['Intercept'])

In [ ]:
# logr_gender.intercept_ = logr_gender.intercept_ + 1

logr_nogender.intercept_ = logr_nogender.intercept_ + 1

credit_full['ApprovedLRgender'] = logr_gender.predict(X_gender)
credit_full['ApprovedLRnogender'] = logr_nogender.predict(X_nogender)


In [ ]:
credit_full.groupby('Gender').mean()

# Bootstrapping, Age, Employment and LogIncome

In [ ]:
B = 1000
n = len(credit_sorted)

beta0star = np.zeros(B)
beta1star = np.zeros(B)
beta2star = np.zeros(B)
beta3star = np.zeros(B)


for i in range(B):
    credit_sample = credit_sorted.sample(n, replace=True)
    X = credit_sample[['Age', 'Employed', 'LogIncome']].to_numpy(copy=True) 
    y = credit_sample['Approved'].to_numpy()
    clf = LogisticRegression().fit(X, y)
    beta0star[i] = clf.intercept_[0]
    beta1star[i] = clf.coef_[0][0]
    beta2star[i] = clf.coef_[0][1]
    beta3star[i] = clf.coef_[0][2]
  
Odds_star = pd.Series(np.exp(beta0star))
OR_age_star = pd.Series(np.exp(beta1star))
OR_employment_star = pd.Series(np.exp(beta2star))
OR_logincome_star = pd.Series(np.exp(beta3star))

In [ ]:
plt.figure(figsize=[6,2], dpi=300)

plt.subplot(1, 4, 1)
plt.hist(np.exp(beta0star), bins=20, density=True)
plt.xlabel('odds (Intercept)')
plt.vlines(Odds_star.quantile([0.05, 0.95]), 0, 10, color='orange')


plt.subplot(1, 4, 2)
plt.hist(np.exp(beta1star), bins=20, density=True)
plt.xlabel('OR (Year of age)')
plt.vlines(OR_age_star.quantile([0.05, 0.95]), 0, 45, color='orange')

plt.subplot(1, 4, 3)
plt.hist(np.exp(beta2star), bins=20, density=True)
plt.vlines(OR_employment_star.quantile([0.05, 0.95]), 0, 0.5, color='orange')
plt.xlabel('OR (Employment)')

plt.subplot(1, 4, 4)
plt.hist(np.exp(beta3star), bins=20, density=True)
plt.vlines(OR_logincome_star.quantile([0.05, 0.95]), 0, 0.5, color='orange')
plt.xlabel('OR (Log Income)')


plt.tight_layout()


In [ ]:
OR_age_star.quantile([0.05, 0.95])


In [ ]:
OR_employment_star.quantile([0.05, 0.95])

In [ ]:
OR_logincome_star.quantile([0.05, 0.95])